EDAF75 - notebook for lecture 10
================================

**Author:** Christian Söderberg



## Lecture 10: Roundup



### Initial incantations



In [1]:
%load_ext sql

In [1]:
%config SqlMagic.displaylimit = None

In [1]:
%sql sqlite:///lect10.sqlite

In [1]:
%%sql
PRAGMA foreign_keys=ON;

### SQL injection



First we define a simple database for our friends:



In [1]:
%%sql
DROP TABLE IF EXISTS friends;
CREATE TABLE friends (
  name         TEXT
);

We then write some Python code for adding friends to the
database:



In [1]:
import sqlite3


conn = sqlite3.connect('lect10.sqlite')


def get_friends():
    c = conn.cursor()
    c.execute(
        "SELECT name "
        "FROM   friends "
    )
    return [name for name, in c]


def show_all():
    print('==== All friends ====')
    for name in get_friends():
        print(name)
    print('---------------------')


def add_friend(name):
    statement = "INSERT INTO friends(name) VALUES ('" + name + "');"
    c = conn.cursor()
    c.executescript(statement)
    conn.commit()
    

def add_friends():
    name = input('Name: ')
    if len(name) > 0:
        add_friend(name)
        show_all()
        add_friends()


def main():
    add_friends()


main()

### Limitations of SQL



****Exercise:**** Define a table with employees of a company,
and information about their immediate supervisors.



In [1]:
%%sql
DROP TABLE IF EXISTS employees;
CREATE TABLE employees (
  employee_id    INT,
  name           TEXT,
  supervisor_id  INT,
  PRIMARY KEY    (employee_id)
);

INSERT
INTO   employees(employee_id, name, supervisor_id)
VALUES (1, 'Liv', 0),
       (2, 'Adam', 1),
       (3, 'Ida', 1),
       (4, 'Hans', 3),
       (5, 'Emma', 1),
       (6, 'Filip', 5),
       (7, 'Gabriel', 4),
       (8, 'Hanna', 2),
       (9, 'Greta', 7);

****Exercise:**** Write a query which finds the name of the
immediate supervisor of all employees.



In [1]:
%%sql

****Exercise:**** Write a query which finds the names of the
supervisors of the supervisors of all employees.



In [1]:
%%sql

****Exercise:**** Write a query which finds all the supervisors
(transitively) of an employee.

This is a kind of query which was virtually impossible until
recursive CTE's were introduced in SQL. We can easily solve
the problem in Python:



In [1]:
import sqlite3

db = sqlite3.connect("lect10.sqlite")

def find_supervisors(original_employee_id):
    pass
    

find_supervisors(7)

But nowadays we can also do it in SQLite3, we can get some
inspiration from the following recursive CTE which generates
the numbers 1..10:



In [1]:
%%sql
WITH RECURSIVE enumeration(x) AS (
  VALUES(1)
  UNION
  SELECT x+1
  FROM   enumeration
  WHERE  x<10
)
SELECT x FROM enumeration;

Coincidentally, SQLite recently got a function
`generate_series` which works like:



In [1]:
%%sql
WITH RECURSIVE generate_series(value) AS (
  SELECT $start
  UNION ALL
  SELECT value+$step FROM generate_series
   WHERE value+$step<=$end
) ...

so, to generate all odd numbers from 1 to 9, we can write:



In [1]:
%%sql
SELECT   value
FROM     generate_series(1, 9, 2)

And to get 10 random numbers, we can write:



In [1]:
%%sql
SELECT   random()
FROM     generate_series(1, 10)

But recursive queries are still useful, as we'll see below&#x2026;

****Example:**** Use the technique above to implement a recursive query which finds all the supervisors of Greta.



In [1]:
%%sql
WITH RECURSIVE supervisors(id) AS (
  VALUES (7)
  UNION
  SELECT supervisor_id
  FROM   employees
         JOIN supervisors ON id = employee_id
)
SELECT id
FROM   supervisors

****Home work:**** Use the technique above to implement a
recursive query which finds all the subordinates of Greta.



In [1]:
%%sql

Using recursive CTE's allows us to do surprising things &#x2013;
try to guess what this query gives us:



In [1]:
%%sql
WITH RECURSIVE
  xaxis(x) AS (VALUES(-2.0) UNION ALL SELECT x+0.05 FROM xaxis WHERE x<1.2),
  yaxis(y) AS (VALUES(-1.0) UNION ALL SELECT y+0.1 FROM yaxis WHERE y<1.0),
  m(iter, cx, cy, x, y) AS (
    SELECT 0, x, y, 0.0, 0.0 FROM xaxis, yaxis
    UNION ALL
    SELECT iter+1, cx, cy, x*x-y*y + cx, 2.0*x*y + cy FROM m 
     WHERE (x*x + y*y) < 4.0 AND iter<28
  ),
  m2(iter, cx, cy) AS (
    SELECT max(iter), cx, cy FROM m GROUP BY cx, cy
  ),
  a(t) AS (
    SELECT group_concat( substr(' .+*#', 1+min(iter/7,4), 1), '') 
    FROM m2 GROUP BY cy
  )
SELECT group_concat(rtrim(t),x'0a') FROM a;

### Self joins, and what happens when a foreign key is removed



In the queries above we joined the table `employees` with
itself, it is called a <u>self join</u>, and we normally do it
using aliases (as above). Note that we in this case have a
foreign key which is in the same table.



In [1]:
%%sql
DROP TABLE IF EXISTS employees;
CREATE TABLE employees (
  employee_id    INT,
  name           TEXT,
  supervisor_id  INT,
  PRIMARY KEY (employee_id),
  FOREIGN KEY (supervisor_id)
    REFERENCES employees(employee_id)
    ON DELETE CASCADE
);

PRAGMA foreign_keys = OFF;

INSERT
INTO   employees(employee_id, name, supervisor_id)
VALUES (1, 'Liv', 0),
       (2, 'Adam', 1),
       (3, 'Ida', 1),
       (4, 'Hans', 3),
       (5, 'Emma', 1),
       (6, 'Filip', 5),
       (7, 'Gabriel', 4),
       (8, 'Hanna', 2),
       (9, 'Greta', 7);

PRAGMA foreign_keys = ON;

Before removing Ida:



In [1]:
%%sql
SELECT employee_id, name
FROM   employees;

&#x2026; and after removing Ida:



In [1]:
%%sql
DELETE
FROM   employees
WHERE  name = 'Ida';

SELECT employee_id, name
FROM   employees;

### BTW &#x2013; another usesful things we can do with CTEs



Sometimes we want to create a view with some simple values,
let's say we want the some small primes in a view
`small_primes`. Using a CTE and the `VALUES` statement, we
can write:



In [1]:
%%sql
WITH small_primes(n) AS (
    VALUES (2), (3), (5), (7), (11), (13)
)
SELECT n
FROM   small_primes

We've seen that using invented keys forces us to join in
places where we otherwise could have used a natural key.  If
`s_name` had been the key in `students`, we could have added
applications easily using:



In [1]:
INSERT
INTO   applications(s_name, c_name, major)
VALUES ('Bob', 'Stanford', 'CS'),
       ('Doris', 'Berkeley', 'EE');

But the key in `students` is `s_id`, hence we need `s_id` to
insert our applications &#x2013; fortunately we can use a
`WITH`-statement to emulate the insertion above:



In [1]:
%%sql
WITH input_data(s_name, c_name, major) AS (
  VALUES ('Bob', 'Stanford', 'CS'),
         ('Doris', 'Berkeley', 'EE')
)
INSERT
INTO   applications(s_id, c_name, major)
SELECT s_id, c_name, major
FROM   input_data
JOIN   students
USING  (s_name);

SELECT *
FROM   students
JOIN   applications
USING  (s_id)
WHERE  s_name IN ('Bob', 'Doris');

and correspondingly:



In [1]:
%%sql
WITH names_to_delete(s_name) AS (
  VALUES ('Bob'),
         ('Doris')
)
DELETE
FROM    applications
WHERE   s_id IN (
  SELECT s_id
  FROM   students
  JOIN   names_to_delete
  USING  (s_name)
);

SELECT *
FROM   students
JOIN   applications
USING  (s_id);

Observe that this only works if the names are unique, if we
had duplicates, every 'Bob' and 'Doris' would apply, and
<u>all</u> students with the name 'Bob' or 'Doris' should be
removed afterwards.

